In [29]:
import os, sys, re, datetime, shutil, copy, subprocess
import numpy as np
import astropy.units as u
from astropy.table import Table
from collections import OrderedDict
sys.path.insert(1, os.path.join(os.path.dirname(os.getcwd()), 'utils'))
radex_bin_path = os.path.expanduser('~/Cloud/Github/Crab.Toolkit.michi2.make.libs/make_lib_LVG/01_RadiativeTransferCode/RADEX/bin/radex_LVG')
radex_data_path = os.path.expanduser('~/Cloud/Github/Crab.Toolkit.michi2.make.libs/make_lib_LVG/01_RadiativeTransferCode/RADEX/data')
radex_calc_path = os.path.expanduser('~/Cloud/GitLab/COExcitation/tmp/calc_radex') # '/tmp/calc_radex'
LTE_calc_path = os.path.expanduser('~/Cloud/GitLab/COExcitation/tmp/calc_LTE')

In [30]:
import moldata
import importlib
importlib.reload(moldata)

CO = moldata.CO()
print(CO)

CI = moldata.CI()
print(CI)

Loading "/Users/dzliu/Cloud/GitLab/COExcitation/data/co.dat"
collision_partner: para-H2
collision_partner: ortho-H2
Species: CO
  Levels: 41 levels
          J=0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32
  Transitions: 40 transitions
  Collisions: 2 partners, 820 transitions
Loading "/Users/dzliu/Cloud/GitLab/COExcitation/data/catom.dat"
collision_partner: 5 C + H  ! Launay & Roueff 1977
collision_partner: 4 C + e  !  from Johnson, Burke, & Kingston 1987, JPhysB, 20, 2553
collision_partner: 7 C + H+  !  Roueff & Le Bourlot 1990, A&A, 236, 515
collision_partner: 6 C + He  !  Staemmler, V., Flower, D.R. 1991, J. Phys. B, 24, 2343
collision_partner: para-H2
collision_partner: ortho-H2
Species: CI
  Levels: 3 levels
  Transitions: 3 transitions
  Collisions: 6 partners, 3 transitions


In [31]:
# User defined global parameters

list_of_N_CO = 10**np.arange(17.0, 20.0+0.25, 0.25)
#list_of_X_CICO = np.arange(0.05, 1.0+0.05, 0.05)
list_of_X_CICO = np.arange(0.05, 3.00+0.05, 0.05)
#list_of_X_CICO = np.logspace(np.log10(0.05), np.log10(5.00), num=100, endpoint=True) #<TODO># tune this range
list_of_n_H2 = [1e2, 1e3, 1e4, 1e5, 1e6]
#list_of_T_kin = [10., 15., 20., 25., 50., 100., 200., 300.] # for CI collison rates only exist for >= 10 K
list_of_T_kin = [10., 15., 20., 25., 30., 40., 50., 100., 200., 300.] # for CI collison rates only exist for >= 10 K
#line_width = 4. #<TODO># manually set and run for: 3. 4. 10. 15. 20. 30. 50. 60. 70. 90.
#line_width = 50. #<TODO><20220111># manually set and run for: 50.
#line_width = 70. #<TODO><20220112># manually set and run for: 70.
#line_width = 20. #<TODO><20220112># manually set and run for: 20.
line_width = 60. #<TODO><20220112># manually set and run for: 60.

out_table_name = 'out_table_RADEX_R_CI10CO21_sim_XCICO_dv_%gkms'%(line_width)
out_figure_name = 'Plot_RADEX_RCI10CO21_nonLTE_LTE_ratio_sim_XCICO_dv_%gkms'%(line_width)


In [32]:
# Define function to compute non-LTE solutions for one (T_kin, N_CO/line_width, n_H2, X_CICO)

def calc_one_RADEX(
        T_kin = 25., 
        N_CO = 1e18, 
        X_CICO = 0.2, 
        n_H2 = 1e2, 
        d_V = 5., 
        T_CMB = 2.72548, 
        overwrite = False, 
    ):
    # 
    global radex_bin_path
    global radex_data_path
    global radex_calc_path
    # 
    # prepare working directory
    T_kin_str = '%.0f'%(T_kin)
    N_CO_str = re.sub(r'(.*)(e)(\+0|\+)([0-9]+.*)', r'\1\2\4', '%.2e'%(N_CO))
    n_H2_str = re.sub(r'(.*)(e)(\+0|\+)([0-9]+.*)', r'\1\2\4', '%.1e'%(n_H2))
    d_V_str = '%.1f'%(d_V)
    calc_name = 'calc_T_kin_%s_N_CO_%s_n_H2_%s_d_V_%s'%(T_kin_str, N_CO_str, n_H2_str, d_V_str)
    working_dir = os.path.join(radex_calc_path, calc_name)
    if not os.path.isdir(working_dir):
        os.makedirs(working_dir)
    if not os.path.isdir(working_dir):
        raise Exception('Error! Could not create dir: ' + working_dir)
    
    # copy mol./atom. data files
    if not os.path.isfile(os.path.join(radex_calc_path, 'co.dat')):
        shutil.copy2(os.path.join(radex_data_path, 'co.dat'), os.path.join(radex_calc_path, 'co.dat'))
    if not os.path.isfile(os.path.join(radex_calc_path, 'catom.dat')):
        shutil.copy2(os.path.join(radex_data_path, 'catom.dat'), os.path.join(radex_calc_path, 'catom.dat'))
    
    # prepare radex input files
    if os.path.isfile(os.path.join(working_dir, 'co.inp')) and overwrite:
        shutil.move(os.path.join(working_dir, 'co.inp'), os.path.join(working_dir, 'co.inp.bak'))
    if os.path.isfile(os.path.join(working_dir, 'co.out')) and overwrite:
        shutil.move(os.path.join(working_dir, 'co.out'), os.path.join(working_dir, 'co.out.bak'))
    if not os.path.isfile(os.path.join(working_dir, 'co.inp')):
        with open(os.path.join(working_dir, 'co.inp'), 'w') as fp:
            fp.write('../co.dat\n')
            fp.write('co.out\n')
            fp.write('100 1900\n') # GHz range
            fp.write('%s\n'%(T_kin)) # 
            fp.write('2\n') # collision partner number
            fp.write('o-H2\n')
            fp.write('%.10e\n'%(n_H2 * 0.75)) # 2371708.245
            fp.write('p-H2\n')
            fp.write('%.10e\n'%(n_H2 * 0.25)) # 790569.415
            fp.write('%s\n'%(T_CMB))
            fp.write('%.10e\n'%(N_CO))
            fp.write('%s\n'%(d_V))
            fp.write('0\n\n') # do not do another calc
    
    # run radex to produce the output file if it does not exist
    if not os.path.isfile(os.path.join(working_dir, 'co.out')):
        command_str = 'cd "%s"; %s < %s > %s'%(working_dir, radex_bin_path, 'co.inp', 'co.log')
        print('command_str', command_str)
        subprocess.call(command_str, shell=True, executable='/bin/bash')
    
    # prepare CI file name, which includes a suffix indicating the CI/CO intrinsic abundance ratio
    X_CICO_str = '%.2f'%(X_CICO)
    CI_filename = 'ci_X_CICO_%s'%(X_CICO_str)
    
    # prepare radex input file for CI calculation
    if os.path.isfile(os.path.join(working_dir, CI_filename+'.inp')) and overwrite:
        shutil.move(os.path.join(working_dir, CI_filename+'.inp'), os.path.join(working_dir, CI_filename+'.inp.bak'))
    if os.path.isfile(os.path.join(working_dir, CI_filename+'.out')) and overwrite:
        shutil.move(os.path.join(working_dir, CI_filename+'.out'), os.path.join(working_dir, CI_filename+'.out.bak'))
    if not os.path.isfile(os.path.join(working_dir, CI_filename+'.inp')):
        with open(os.path.join(working_dir, CI_filename+'.inp'), 'w') as fp:
            fp.write('../catom.dat\n')
            fp.write(CI_filename+'.out\n')
            fp.write('100 1900\n') # GHz range
            fp.write('%s\n'%(T_kin)) # 
            fp.write('2\n') # collision partner number
            fp.write('o-H2\n')
            fp.write('%.10e\n'%(n_H2 * 0.75)) # 2371708.245
            fp.write('p-H2\n')
            fp.write('%.10e\n'%(n_H2 * 0.25)) # 790569.415
            fp.write('%s\n'%(T_CMB))
            fp.write('%.10e\n'%(N_CO * X_CICO))
            fp.write('%s\n'%(d_V))
            fp.write('0\n\n') # 0 means ends this calculation.
    
    # run radex to produce the output file for CI if it does not exist
    if not os.path.isfile(os.path.join(working_dir, CI_filename+'.out')):
        command_str = 'cd "%s"; %s < %s > %s'%(working_dir, radex_bin_path, CI_filename+'.inp', CI_filename+'.log')
        print('command_str', command_str)
        subprocess.call(command_str, shell=True, executable='/bin/bash')
    
    # read output files
    output_dict = {}
    
    output_dict['CO'] = OrderedDict([ 
        ('J_UP',[]), 
        ('J_LOW',[]), 
        ('E_UP',[]), 
        ('FREQ',[]), 
        ('WAVE',[]), 
        ('T_ex',[]), 
        ('tau_0',[]), 
        ('T_RJ',[]), 
        ('Pop_u',[]), 
        ('Pop_l',[]), 
        ('Flux_Kkms',[]), 
        ('Flux_ergcm2s',[]), 
    ])
    
    output_dict['CI'] = OrderedDict([ 
        ('J_UP',[]), 
        ('J_LOW',[]), 
        ('E_UP',[]), 
        ('FREQ',[]), 
        ('WAVE',[]), 
        ('T_ex',[]), 
        ('tau_0',[]), 
        ('T_RJ',[]), 
        ('Pop_u',[]), 
        ('Pop_l',[]), 
        ('Flux_Kkms',[]), 
        ('Flux_ergcm2s',[]), 
    ])
    
    with open(os.path.join(working_dir, 'co.out'), 'r') as fp:
        for line_str in fp:
            if line_str.startswith('#') or line_str.startswith('*'):
                continue
            if line_str.startswith('J_UP') or re.match(r'^\s+(LINE|\(K\)).*', line_str):
                continue
            line_split = line_str.split()
            line_split = [t for t in line_split if t != '--']
            if len(line_split) >= 12:
                for icol, key in enumerate(output_dict['CO'].keys()):
                    output_dict['CO'][key].append(float(line_split[icol]))
    
    with open(os.path.join(working_dir, CI_filename+'.out'), 'r') as fp:
        for line_str in fp:
            if line_str.startswith('#') or line_str.startswith('*'):
                continue
            if line_str.startswith('J_UP') or re.match(r'^\s+(LINE|\(K\)).*', line_str):
                continue
            line_split = line_str.split()
            line_split = [t for t in line_split if t != '--']
            if len(line_split) >= 12:
                for icol, key in enumerate(output_dict['CI'].keys()):
                    output_dict['CI'][key].append(float(line_split[icol]))
    
    # return
    return output_dict

# test
out_dict_radex = None
if False:
    out_dict_radex = calc_one_RADEX(
            T_kin = list_of_T_kin[0], 
            N_CO = list_of_N_CO[0], 
            X_CICO = list_of_X_CICO[0], 
            n_H2 = list_of_n_H2[0], 
            d_V = line_width, 
            overwrite = True, 
        )
out_dict_radex

In [33]:
# Define function to compute non-LTE solutions for one (T_kin, N_CO/line_width, n_H2, X_CICO)

def run_for_one_input_set(var_dict):
    # 
    global radex_calc_path
    global LTE_calc_path
    # 
    # read input variables
    CO = var_dict['CO'] # the moldata class object
    CI = var_dict['CI'] # the moldata class object
    N_CO = var_dict['N_CO'] # species_column_density of CO
    N_CI = var_dict['N_CI'] # species_column_density of CI
    X_CICO = N_CI/N_CO
    d_V = var_dict['d_V']
    T_kin = var_dict['T_kin']
    n_H2 = var_dict['n_H2']
    collision_partner_densities = var_dict['collision_partner_densities']
    # 
    # prepare working directory for LTE calculation temporary files
    T_kin_str = '%.0f'%(T_kin.to(u.K).value)
    N_CO_str = re.sub(r'(.*)(e)(\+0|\+)([0-9]+.*)', r'\1\2\4', '%.2e'%(N_CO.to(u.cm**(-2)).value))
    n_H2_str = re.sub(r'(.*)(e)(\+0|\+)([0-9]+.*)', r'\1\2\4', '%.1e'%(n_H2.to(u.cm**(-3)).value))
    d_V_str = '%.1f'%(d_V.to(u.km/u.s).value)
    calc_name = 'calc_T_kin_%s_N_CO_%s_n_H2_%s_d_V_%s'%(T_kin_str, N_CO_str, n_H2_str, d_V_str)
    LTE_working_dir = os.path.join(LTE_calc_path, calc_name)
    if not os.path.isdir(LTE_working_dir):
        os.makedirs(LTE_working_dir)
    if not os.path.isdir(LTE_working_dir):
        raise Exception('Error! Could not create dir: ' + LTE_working_dir)
    
    # prepare CI file name, which includes a suffix indicating the CI/CO intrinsic abundance ratio
    X_CICO_str = '%.2f'%(X_CICO)
    CI_filename = 'ci_X_CICO_%s'%(X_CICO_str)
    
    # check CI LTE table file, read it if exists, otherwise do the computation
    out_table_file_CI_LTE = os.path.join(LTE_working_dir, CI_filename + '.csv')
    if os.path.isfile(out_table_file_CI_LTE):
        out_table_CI_LTE = Table.read(out_table_file_CI_LTE, format='csv')
    else:
        # use dzliu ../utils/moldata.py class to compute LTE for CI
        CI.evaluate_level_populations(species_column_density = N_CI, 
                                      line_width = d_V, 
                                      T_kin = T_kin, 
                                      collision_partner_densities = collision_partner_densities, 
                                      verbose = False, 
                                      silent = True, 
                                      LTE = True)
        out_table_CI_LTE = CI.get_solved_transition_properties()
        out_table_CI_LTE.write(out_table_file_CI_LTE, format='csv')
    
    # check CO LTE table file, read it if exists, otherwise do the computation
    out_table_file_CO_LTE = os.path.join(LTE_working_dir, 'co.csv')
    if os.path.isfile(out_table_file_CO_LTE):
        out_table_CO_LTE = Table.read(out_table_file_CO_LTE, format='csv')
    else:
        # use dzliu ../utils/moldata.py class to compute LTE for CO
        CO.evaluate_level_populations(species_column_density = N_CO, 
                                      line_width = d_V, 
                                      T_kin = T_kin, 
                                      collision_partner_densities = collision_partner_densities, 
                                      verbose = False, 
                                      silent = True, 
                                      LTE = True)
        out_table_CO_LTE = CO.get_solved_transition_properties()
        out_table_CO_LTE.write(out_table_file_CO_LTE, format='csv')
    
    # do the RADEX NonLTE calculation
    # this will also check if cached output files exist or not and try to load them
    out_dict_radex = calc_one_RADEX(
        T_kin = T_kin.value, 
        N_CO = N_CO.value, 
        X_CICO = N_CI.value/N_CO.value, 
        n_H2 = n_H2.value, 
        d_V = d_V.value, 
        overwrite = False, 
    )
    out_table_CI_NonLTE = out_dict_radex['CI']
    out_table_CO_NonLTE = out_dict_radex['CO']
    
    # prepare output result dict
    res_dict = OrderedDict()
    res_dict['N_CO'] = N_CO
    res_dict['N_CI'] = N_CI
    res_dict['X_CICO'] = N_CI/N_CO
    res_dict['T_kin'] = T_kin
    res_dict['n_H2'] = n_H2
    res_dict['d_V'] = d_V
    
    res_dict['Flux_Kkms_CO10_NonLTE'] = out_table_CO_NonLTE['Flux_Kkms'][0]
    res_dict['Flux_Kkms_CO10_LTE'] = out_table_CO_LTE['Flux_Kkms'][0]
    res_dict['Flux_Kkms_CO21_NonLTE'] = out_table_CO_NonLTE['Flux_Kkms'][1]
    res_dict['Flux_Kkms_CO21_LTE'] = out_table_CO_LTE['Flux_Kkms'][1]
    res_dict['Flux_Kkms_CI10_NonLTE'] = out_table_CI_NonLTE['Flux_Kkms'][0]
    res_dict['Flux_Kkms_CI10_LTE'] = out_table_CI_LTE['Flux_Kkms'][0]
    res_dict['Flux_Kkms_CI21_NonLTE'] = out_table_CI_NonLTE['Flux_Kkms'][1]
    res_dict['Flux_Kkms_CI21_LTE'] = out_table_CI_LTE['Flux_Kkms'][1]
    
    res_dict['tau_0_CO10_NonLTE'] = out_table_CO_NonLTE['tau_0'][0]
    res_dict['tau_0_CO10_LTE'] = out_table_CO_LTE['tau_0'][0]
    res_dict['tau_0_CO21_NonLTE'] = out_table_CO_NonLTE['tau_0'][1]
    res_dict['tau_0_CO21_LTE'] = out_table_CO_LTE['tau_0'][1]
    res_dict['tau_0_CI10_NonLTE'] = out_table_CI_NonLTE['tau_0'][0]
    res_dict['tau_0_CI10_LTE'] = out_table_CI_LTE['tau_0'][0]
    res_dict['tau_0_CI21_NonLTE'] = out_table_CI_NonLTE['tau_0'][1]
    res_dict['tau_0_CI21_LTE'] = out_table_CI_LTE['tau_0'][1]
    
    res_dict['Pop_u_CO10_NonLTE'] = out_table_CO_NonLTE['Pop_u'][0]
    res_dict['Pop_u_CO10_LTE'] = out_table_CO_LTE['Pop_u'][0]
    res_dict['Pop_u_CO21_NonLTE'] = out_table_CO_NonLTE['Pop_u'][1]
    res_dict['Pop_u_CO21_LTE'] = out_table_CO_LTE['Pop_u'][1]
    res_dict['Pop_u_CI10_NonLTE'] = out_table_CI_NonLTE['Pop_u'][0]
    res_dict['Pop_u_CI10_LTE'] = out_table_CI_LTE['Pop_u'][0]
    res_dict['Pop_u_CI21_NonLTE'] = out_table_CI_NonLTE['Pop_u'][1]
    res_dict['Pop_u_CI21_LTE'] = out_table_CI_LTE['Pop_u'][1]
    
    res_dict['Pop_l_CO10_NonLTE'] = out_table_CO_NonLTE['Pop_l'][0]
    res_dict['Pop_l_CO10_LTE'] = out_table_CO_LTE['Pop_l'][0]
    res_dict['Pop_l_CO21_NonLTE'] = out_table_CO_NonLTE['Pop_l'][1]
    res_dict['Pop_l_CO21_LTE'] = out_table_CO_LTE['Pop_l'][1]
    res_dict['Pop_l_CI10_NonLTE'] = out_table_CI_NonLTE['Pop_l'][0]
    res_dict['Pop_l_CI10_LTE'] = out_table_CI_LTE['Pop_l'][0]
    res_dict['Pop_l_CI21_NonLTE'] = out_table_CI_NonLTE['Pop_l'][1]
    res_dict['Pop_l_CI21_LTE'] = out_table_CI_LTE['Pop_l'][1]
    
    res_dict['T_ex_CO10_NonLTE'] = out_table_CO_NonLTE['T_ex'][0]
    res_dict['T_ex_CO10_LTE'] = out_table_CO_LTE['T_ex'][0]
    res_dict['T_ex_CO21_NonLTE'] = out_table_CO_NonLTE['T_ex'][1]
    res_dict['T_ex_CO21_LTE'] = out_table_CO_LTE['T_ex'][1]
    res_dict['T_ex_CI10_NonLTE'] = out_table_CI_NonLTE['T_ex'][0]
    res_dict['T_ex_CI10_LTE'] = out_table_CI_LTE['T_ex'][0]
    res_dict['T_ex_CI21_NonLTE'] = out_table_CI_NonLTE['T_ex'][1]
    res_dict['T_ex_CI21_LTE'] = out_table_CI_LTE['T_ex'][1]
    
    try:
        res_dict['R_CI10CO21_NonLTE'] = out_table_CI_NonLTE['Flux_Kkms'][0] / out_table_CO_NonLTE['Flux_Kkms'][1]
    except:
        res_dict['R_CI10CO21_NonLTE'] = np.nan
    try:
        res_dict['R_CI10CO21_LTE'] = out_table_CI_LTE['Flux_Kkms'][0] / out_table_CO_LTE['Flux_Kkms'][1]
    except:
        res_dict['R_CI10CO21_LTE'] = np.nan
    
    # return the result dict
    return res_dict

# test
res_dict = None
if True:
    res_dict = run_for_one_input_set({
                'CO': CO, 
                'CI': CI, 
                'T_kin': list_of_T_kin[0] * u.K, 
                'N_CO': list_of_N_CO[0] * u.cm**(-2), 
                'N_CI': list_of_N_CO[0] * list_of_X_CICO[0] * u.cm**(-2), 
                'X_CICO': list_of_X_CICO[0], 
                'n_H2': list_of_n_H2[0] * u.cm**(-3), 
                'd_V': line_width * u.km/u.s, 
                'collision_partner_densities': {'ortho-H2': 0.75 * list_of_n_H2[0] * u.cm**(-3), 
                                                'para-H2': 0.25 * list_of_n_H2[0] * u.cm**(-3)}, 
            }
        )
res_dict

OrderedDict([('N_CO', <Quantity 1.e+17 1 / cm2>),
             ('N_CI', <Quantity 5.e+15 1 / cm2>),
             ('X_CICO', <Quantity 0.05>),
             ('T_kin', <Quantity 10. K>),
             ('n_H2', <Quantity 100. 1 / cm3>),
             ('d_V', <Quantity 60. km / s>),
             ('Flux_Kkms_CO10_NonLTE', 22.25),
             ('Flux_Kkms_CO10_LTE', 95.07399932989637),
             ('Flux_Kkms_CO21_NonLTE', 4.313),
             ('Flux_Kkms_CO21_LTE', 124.0145703589379),
             ('Flux_Kkms_CI10_NonLTE', 0.02143),
             ('Flux_Kkms_CI10_LTE', 0.18265044024496607),
             ('Flux_Kkms_CI21_NonLTE', 0.0002564),
             ('Flux_Kkms_CI21_LTE', 0.007801463247580553),
             ('tau_0_CO10_NonLTE', 1.18),
             ('tau_0_CO10_LTE', 0.25349537970483915),
             ('tau_0_CO21_NonLTE', 0.5535),
             ('tau_0_CO21_LTE', 0.45931404502823836),
             ('tau_0_CI10_NonLTE', 0.001606),
             ('tau_0_CI10_LTE', 0.0011664008848587468),
    

In [34]:
# Run the calculation loop

print('datetime.datetime.now()', datetime.datetime.now())

# Loop
var_dict = {'CO': CO, 'CI': CI}
out_dict = None
for idx_X_CICO, X_CICO in enumerate(list_of_X_CICO):
    for idx_N_CO, N_CO in enumerate(list_of_N_CO):
        for idx_n_H2, n_H2 in enumerate(list_of_n_H2):
            for idx_T_kin, T_kin in enumerate(list_of_T_kin):
                print('Parameters: (T_kin, n_H2, N_CO, X_CICO) = (%5.1f, %5.2f, %4.1f, %4.2f)'%(
                        T_kin, 
                        np.log10(n_H2), 
                        np.log10(N_CO), 
                        X_CICO ) + \
                      ' | %02d/%02d, %02d/%02d, %02d/%02d, %02d/%02d |'%(
                        idx_T_kin+1, len(list_of_T_kin), 
                        idx_n_H2+1, len(list_of_n_H2), 
                        idx_N_CO+1, len(list_of_N_CO), 
                        idx_X_CICO+1, len(list_of_X_CICO) )
                    )
                var_dict['N_CO'] = N_CO * u.cm**(-2)
                var_dict['N_CI'] = X_CICO * N_CO * u.cm**(-2) # CI/CO intrinsic abundance ratio
                var_dict['X_CICO'] = X_CICO
                var_dict['d_V'] = line_width * u.km/u.s
                var_dict['T_kin'] = T_kin * u.K
                var_dict['n_H2'] = n_H2 * u.cm**(-3)
                var_dict['collision_partner_densities'] = {'ortho-H2': 0.75 * n_H2 * u.cm**(-3), 
                                                           'para-H2': 0.25 * n_H2 * u.cm**(-3)}
                
                res_dict = run_for_one_input_set(var_dict)
                
                if out_dict is None:
                    out_dict = OrderedDict()
                    for key in res_dict:
                        out_dict[key] = [res_dict[key]]
                else:
                    for key in res_dict:
                        out_dict[key].append(res_dict[key])
        
        #out_table_cache = Table(out_dict)
        #out_table_cache.write(out_table_name + '.cache.csv', format='csv', overwrite=True)
        
print('datetime.datetime.now()', datetime.datetime.now())

out_table = Table(out_dict)
out_table

datetime.datetime.now() 2022-01-13 13:49:10.159855
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  2.00, 17.0, 0.05) | 01/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  2.00, 17.0, 0.05) | 02/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  2.00, 17.0, 0.05) | 03/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  2.00, 17.0, 0.05) | 04/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  2.00, 17.0, 0.05) | 05/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  2.00, 17.0, 0.05) | 06/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  2.00, 17.0, 0.05) | 07/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  2.00, 17.0, 0.05) | 08/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  2.00, 17.0, 0.05) | 09/10, 01/05, 01/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,

Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  5.00, 17.2, 0.05) | 05/10, 04/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  5.00, 17.2, 0.05) | 06/10, 04/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  5.00, 17.2, 0.05) | 07/10, 04/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  5.00, 17.2, 0.05) | 08/10, 04/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  5.00, 17.2, 0.05) | 09/10, 04/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  5.00, 17.2, 0.05) | 10/10, 04/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  6.00, 17.2, 0.05) | 01/10, 05/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  6.00, 17.2, 0.05) | 02/10, 05/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  6.00, 17.2, 0.05) | 03/10, 05/05, 02/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  6.00, 17.2, 0.05) | 04/10, 05/05, 02/13, 01/60 |


Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  4.00, 17.8, 0.05) | 10/10, 03/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  5.00, 17.8, 0.05) | 01/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  5.00, 17.8, 0.05) | 02/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  5.00, 17.8, 0.05) | 03/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  5.00, 17.8, 0.05) | 04/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  5.00, 17.8, 0.05) | 05/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  5.00, 17.8, 0.05) | 06/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  5.00, 17.8, 0.05) | 07/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  5.00, 17.8, 0.05) | 08/10, 04/05, 04/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  5.00, 17.8, 0.05) | 09/10, 04/05, 04/13, 01/60 |


Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  4.00, 18.2, 0.05) | 01/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  4.00, 18.2, 0.05) | 02/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  4.00, 18.2, 0.05) | 03/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  4.00, 18.2, 0.05) | 04/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  4.00, 18.2, 0.05) | 05/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  4.00, 18.2, 0.05) | 06/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  4.00, 18.2, 0.05) | 07/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  4.00, 18.2, 0.05) | 08/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  4.00, 18.2, 0.05) | 09/10, 03/05, 06/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  4.00, 18.2, 0.05) | 10/10, 03/05, 06/13, 01/60 |


Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  2.00, 18.8, 0.05) | 03/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  2.00, 18.8, 0.05) | 04/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  2.00, 18.8, 0.05) | 05/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  2.00, 18.8, 0.05) | 06/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  2.00, 18.8, 0.05) | 07/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  2.00, 18.8, 0.05) | 08/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  2.00, 18.8, 0.05) | 09/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  2.00, 18.8, 0.05) | 10/10, 01/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  3.00, 18.8, 0.05) | 01/10, 02/05, 08/13, 01/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  3.00, 18.8, 0.05) | 02/10, 02/05, 08/13, 01/60 |


...

Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  2.00, 18.2, 3.00) | 06/10, 01/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  2.00, 18.2, 3.00) | 07/10, 01/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  2.00, 18.2, 3.00) | 08/10, 01/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  2.00, 18.2, 3.00) | 09/10, 01/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  2.00, 18.2, 3.00) | 10/10, 01/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  3.00, 18.2, 3.00) | 01/10, 02/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  3.00, 18.2, 3.00) | 02/10, 02/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  3.00, 18.2, 3.00) | 03/10, 02/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  3.00, 18.2, 3.00) | 04/10, 02/05, 06/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  3.00, 18.2, 3.00) | 05/10, 02/05, 06/13, 60/60 |


Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  6.00, 18.5, 3.00) | 04/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  6.00, 18.5, 3.00) | 05/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  6.00, 18.5, 3.00) | 06/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  6.00, 18.5, 3.00) | 07/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  6.00, 18.5, 3.00) | 08/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  6.00, 18.5, 3.00) | 09/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  6.00, 18.5, 3.00) | 10/10, 05/05, 07/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  2.00, 18.8, 3.00) | 01/10, 01/05, 08/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  2.00, 18.8, 3.00) | 02/10, 01/05, 08/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  2.00, 18.8, 3.00) | 03/10, 01/05, 08/13, 60/60 |


Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  2.00, 19.2, 3.00) | 02/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  2.00, 19.2, 3.00) | 03/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  2.00, 19.2, 3.00) | 04/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  2.00, 19.2, 3.00) | 05/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  2.00, 19.2, 3.00) | 06/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  2.00, 19.2, 3.00) | 07/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  2.00, 19.2, 3.00) | 08/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  2.00, 19.2, 3.00) | 09/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  2.00, 19.2, 3.00) | 10/10, 01/05, 10/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  3.00, 19.2, 3.00) | 01/10, 02/05, 10/13, 60/60 |


Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 10.0,  2.00, 19.8, 3.00) | 01/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 15.0,  2.00, 19.8, 3.00) | 02/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 20.0,  2.00, 19.8, 3.00) | 03/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 25.0,  2.00, 19.8, 3.00) | 04/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 30.0,  2.00, 19.8, 3.00) | 05/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 40.0,  2.00, 19.8, 3.00) | 06/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = ( 50.0,  2.00, 19.8, 3.00) | 07/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (100.0,  2.00, 19.8, 3.00) | 08/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (200.0,  2.00, 19.8, 3.00) | 09/10, 01/05, 12/13, 60/60 |
Parameters: (T_kin, n_H2, N_CO, X_CICO) = (300.0,  2.00, 19.8, 3.00) | 10/10, 01/05, 12/13, 60/60 |


<Table length=39000>
  N_CO         N_CI         X_CICO  T_kin     n_H2     d_V   Flux_Kkms_CO10_NonLTE Flux_Kkms_CO10_LTE ... T_ex_CO21_LTE T_ex_CI10_NonLTE T_ex_CI10_LTE T_ex_CI21_NonLTE T_ex_CI21_LTE  R_CI10CO21_NonLTE       R_CI10CO21_LTE   
1 / cm2      1 / cm2                  K     1 / cm3   km / s                                          ...                                                                                                                       
float64      float64       float64 float64  float64  float64        float64             float64       ...    float64        float64         float64        float64         float64          float64               float64       
------- ------------------ ------- ------- --------- ------- --------------------- ------------------ ... ------------- ---------------- ------------- ---------------- ------------- -------------------- ---------------------
  1e+17 5000000000000000.0    0.05    10.0     100.0    60.0                 22.25  95.07399932989637 ...          10.0            5.008          10.0            7.506          10.0 0.004968699281242755 0.0014728143613796118
  1e+17 5000000000000000.0    0.05    15.0     100.0    60.0                 31.03   87.8068903434895 ...          15.0            6.161          15.0            9.907          15.0 0.006731154102735157  0.001877213840818099
  1e+17 5000000000000000.0    0.05    20.0     100.0    60.0                  36.6  76.76841724312892 ...          20.0            7.096          20.0           11.673          20.0  0.00805513784461153  0.002088411139324931
  1e+17 5000000000000000.0    0.05    25.0     100.0    60.0                 40.87  67.09352498666492 ...          25.0            7.785          25.0           13.034          25.0 0.008652246256239601 0.0022353475662573613
  1e+17 5000000000000000.0    0.05    30.0     100.0    60.0                 44.04  59.21040889620593 ...          30.0            8.359          30.0           14.096          30.0 0.009076923076923076  0.002362662945881619
  1e+17 5000000000000000.0    0.05    40.0     100.0    60.0                 48.87  47.61323093725405 ...          40.0            9.261          40.0           15.659          40.0 0.009495384615384616  0.002609748084170743
  1e+17 5000000000000000.0    0.05    50.0     100.0    60.0                 52.43  39.67289048393617 ...          50.0            9.934          50.0           16.777          50.0  0.00960065645514223 0.0028656051754291636
  1e+17 5000000000000000.0    0.05   100.0     100.0    60.0                 63.27 21.459973804942564 ...         100.0            11.93         100.0           19.446         100.0 0.009151056197688322  0.004257227011819035
  1e+17 5000000000000000.0    0.05   200.0     100.0    60.0                 75.46  11.14277797184474 ...         200.0           13.882         200.0           21.372         200.0   0.0078865828705057  0.007206206852224227
  1e+17 5000000000000000.0    0.05   300.0     100.0    60.0                 83.77  7.519774494119079 ...         300.0           15.069         300.0           22.324         300.0 0.006968674698795181  0.010200414446156615
  1e+17 5000000000000000.0    0.05    10.0    1000.0    60.0                 86.12  95.07399932989637 ...          10.0            7.785          10.0             8.62          10.0 0.003152043269230769 0.0014728143613796118
    ...                ...     ...     ...       ...     ...                   ...                ... ...           ...              ...           ...              ...           ...                  ...                   ...
  1e+20              3e+20     3.0   200.0  100000.0    60.0                7745.0  7386.095013826622 ...         200.0          199.597         200.0          197.016         200.0   0.7939983093829248    0.7830923038673775
  1e+20              3e+20     3.0   300.0  100000.0    60.0                6986.0  6206.864414095146 ...         300.0          299.992         300.0    

In [35]:
# Write table to disk

if os.path.isfile(out_table_name):
    shutil.move(out_table_name, out_table_name+'.backup')
out_table.write(out_table_name + '.csv', format='csv', overwrite=True)
#out_table.write(out_table_name + '.dat', format='ascii.fixed_width', delimiter='  ', bookend=True, overwrite=True)
print('Output to "%s"'%(out_table_name + '.csv'))
#print('Output to "%s"'%(out_table_name + '.dat'))

Output to "out_table_RADEX_R_CI10CO21_sim_XCICO_dv_60kms.csv"
